---

# S04E01 : Context managers - The with statement

Cyril Desjouy

---


## 1. Resource management with context managers

The main purpose of a *context manager* is to manage resources. This is why it is used in particular for file reading. Indeed, opening a file consumes a resource and this number of ressources is limited by the OS. 

To open and read the contents of a file, you can usually write:

In [2]:
file = open('quote.txt')
txt = file.read()
file.close()

print(txt)

“Bad programmers worry about the code.
Good programmers worry about data structures and their relationships.”
― Linus Torvalds



With this formulation, it is very easy to forget to close the file with the `close()` method. If the file is open for writing, this can lead to unexpected results. In the case where the file is open for reading, the omission is not so serious, but when it comes to hundreds of files, it can lead to critical situations where the OS limits can be reached, for example. By entrusting resource management to a *context manager*, we ensure that each resource is properly closed. 

Using the `with... as...` instruction, it is possible to return a *context manager* associated with a variable name that will be available throughout the indented block:
```python
with ressource as name:
    do stuff
```

To open a file, simply write:

In [5]:
with open('quote.txt') as file:
    txt = file.read()
    
print(txt)

“Bad programmers worry about the code.
Good programmers worry about data structures and their relationships.”
― Linus Torvalds



## 2. Customized *context managers*

### 2.1. The special methods `__enter__` and `__exit__`

To implement a custom *context manager*, simply write a class containing the special methods `__enter__` and `__exit__`.

* `__enter__` should return an object that will be assigned to the name after `as` (default `None`). It is common to return `self` in order to keep all the features of the class.
* `__exit__` should free up the resources used.

For example:

In [3]:
class context:
    
    def __init__(self):
        print('Init context')
    
    def __enter__(self):
        print('Entering context manager')
        return self
        
    def __exit__(self, *args):
        print('Exiting context manager')

In [4]:
with context() as c:
    print("I'm in!")

Init context
Entering context manager
I'm in!
Exiting context manager


### 2.2. Exception management

The special method `__exit__` actually takes 4 input arguments (hence the presence of the `*args` in the previous example):

* the instance
* `exception_type`: the type of exception raised 
* `exception_value`: the value of the exception raised
* `traceback`: the traceback

The exit mechanism proposed by the *context managers* allows the resource to be closed correctly even if an exception has been raised within the *context manager*. The `__exit__` method can also return a Boolean. If this Boolean is `True`, then the exceptions raised in the indented block will be hidden. The following examples illustrate this:

**Note:** *If an exception is raised in the `__init__` or `__enter__` method then the `__exit__` method will not be executed.*

In [22]:
class context:
    
    def __init__(self, noexception=False):
        self.noexception = noexception
        print('Init context')
    
    def __enter__(self):
        print('Entering context manager')
        return self
        
    def __exit__(self, exception_type, exception_value, traceback):
        
        if exception_type:
            print('type:', exception_type)
            print('value:', exception_value)
            print('traceback', traceback)
        
        print('Exiting context manager')
        return self.noexception
    
    def causes_exception(self):
        """ Deliberately causes an attribute error"""
        a = int('string')

In [23]:
with context(noexception=True) as c:
    c.causes_exeption()

Init context
Entering context manager
type: <class 'AttributeError'>
value: 'context' object has no attribute 'cause_exeption'
traceback <traceback object at 0x7fbe05f7a2d0>
Exiting context manager


In [25]:
with context() as c:
    c.causes_exeption()

Init context
Entering context manager
type: <class 'AttributeError'>
value: 'context' object has no attribute 'causes_exeption'
traceback <traceback object at 0x7fbe05f61370>
Exiting context manager


AttributeError: 'context' object has no attribute 'causes_exeption'

## 3. Use of *context managers*

*Context managers* are commons in the standard library. They are far from being used only for the management of text files. Here are some examples of applications:

* The synchronization primitives of `threading`, `multiprocessing`, and `concurrent.futures` such as `Lock`, `Semaphore`, `Condition`, ... (see notebook on synchronization primitives)
* The zip files (`zipfile.ZipFile)`, tar files (`tarfile.TarFile`), ...
* Network resources
* Decorators
* ...


## References

* [Jeffknupp.com - Python with context manager](https://jeffknupp.com/blog/2016/03/07/python-with-context-managers/)
* [Aly Sivji - Managing ressources with context managers](https://alysivji.github.io/managing-resources-with-context-managers-pythonic.html)

## Application

<div class="alert alert-block alert-info">
Implement a context manager to measure the time spent executing a sequence of instructions. To do this, you will use the function <code>perf_counter()</code> provided by the <code>time</code> module.
</div>